In [1]:
import warnings
warnings.filterwarnings("ignore")

In [2]:
import spacy
import random
import torch
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder
from transformers import BertTokenizer, BertModel
from torch.nn.utils.rnn import pad_sequence
from torch.utils.data import DataLoader, TensorDataset
import torch.nn as nn
import torch.nn.functional as F
import torch.autograd as autograd
import torch.optim as optim
from TorchCRF import CRF

In [3]:
def load_dataset(file_path):
    sentences = []
    labels = []
    
    with open(file_path, 'r') as f:
        lines = f.readlines()
        sentence = []
        
        for line in lines:
            line = line.strip() # remove leading/trailing whitespaces
            if line:
                if not line.startswith('ARG1') and not line.startswith('ARG2') and not line.startswith('REL') and not line.startswith('LOC') and not line.startswith('TIME') and not line.startswith('NONE'):
                    sentence = line
                else:
                    current_label = line
                    sentences.append(sentence)
                    labels.append(current_label)
                    
    return sentences, labels

In [4]:
# load the dataset into a pandas dataframe
sentences, labels = load_dataset('./Dataset/original_cleaned')
df = pd.DataFrame({
    'Sentence': sentences,
    'Labels': labels
})

In [5]:
df.shape

(180517, 2)

In [6]:
df

Sentence  \
0       Simon is quoted as saying `` if you 'd ever se...   
1       Simon is quoted as saying `` if you 'd ever se...   
2       Simon is quoted as saying `` if you 'd ever se...   
3       Simon is quoted as saying `` if you 'd ever se...   
4                            The couple had no children .   
...                                                   ...   
180512  Afterwards Ong wrote : `` Hands holding Tai ch...   
180513  Afterwards Ong wrote : `` Hands holding Tai ch...   
180514  This was the time when Yang Luchan made the Ch...   
180515  This was the time when Yang Luchan made the Ch...   
180516  This was the time when Yang Luchan made the Ch...   

                                                   Labels  
0       ARG1 REL REL ARG2 ARG2 ARG2 ARG2 ARG2 ARG2 ARG...  
1       NONE NONE NONE NONE NONE NONE NONE NONE NONE N...  
2       NONE NONE NONE NONE NONE NONE NONE ARG1 REL TI...  
3       ARG1 NONE NONE REL REL NONE NONE NONE NONE NON...  
4                            ARG1 ARG1 REL ARG2 ARG2 NONE  
...                                                   ...  
180512  NONE NONE NONE NONE NONE ARG1 REL ARG2 ARG2 AR...  
180513  NONE NONE NONE NONE NONE NONE NONE NONE NONE N...  
180514  ARG1 REL ARG2 ARG2 ARG2 ARG2 ARG2 ARG2 ARG2 AR...  
180515  NONE NONE TIME TIME NONE ARG1 ARG1 REL ARG2 AR...  
180516  NONE NONE NONE NONE NONE NONE NONE NONE ARG1 A...  

[180517 rows x 2 columns]

In [7]:
# change this later on !!!!
df = df[:2500]

In [8]:
def remerge_sent(sent):
    # merges tokens which are not separated by white-space
    # does this recursively until no further changes
    changed = True
    while changed:
        changed = False
        i = 0
        while i < sent.__len__() - 1:
            tok = sent[i]
            if not tok.whitespace_:
                ntok = sent[i + 1]
                # in-place operation.
                with sent.retokenize() as retokenizer:
                    retokenizer.merge(sent[i: i + 2])
                changed = True
            i += 1
    return sent

In [9]:
# Tokenize sentences using spacy
nlp = spacy.load('en_core_web_sm')

In [10]:
def check_token_label_length(row):
    doc = nlp(row['Sentence'])
    spacy_sentence = remerge_sent(doc)
    tokens = [token.text for token in spacy_sentence]
    labels = row['Labels'].split()

    is_match = len(tokens) == len(labels)
    return is_match, len(tokens), len(labels), tokens

In [11]:
df[['Token_Label_Match', 'Num_Tokens', 'Num_Labels', 'Tokens']] = df.apply(check_token_label_length, axis=1, result_type="expand")

In [12]:
df.head()

Sentence  \
0  Simon is quoted as saying `` if you 'd ever se...   
1  Simon is quoted as saying `` if you 'd ever se...   
2  Simon is quoted as saying `` if you 'd ever se...   
3  Simon is quoted as saying `` if you 'd ever se...   
4                       The couple had no children .   

                                              Labels  Token_Label_Match  \
0  ARG1 REL REL ARG2 ARG2 ARG2 ARG2 ARG2 ARG2 ARG...               True   
1  NONE NONE NONE NONE NONE NONE NONE NONE NONE N...               True   
2  NONE NONE NONE NONE NONE NONE NONE ARG1 REL TI...               True   
3  ARG1 NONE NONE REL REL NONE NONE NONE NONE NON...               True   
4                       ARG1 ARG1 REL ARG2 ARG2 NONE               True   

   Num_Tokens  Num_Labels                                             Tokens  
0          32          32  [Simon, is, quoted, as, saying, ``, if, you, '...  
1          32          32  [Simon, is, quoted, as, saying, ``, if, you, '...  
2          32          32  [Simon, is, quoted, as, saying, ``, if, you, '...  
3          32          32  [Simon, is, quoted, as, saying, ``, if, you, '...  
4           6           6                [The, couple, had, no, children, .]

In [13]:
# Load the pre-trained BERT tokenizer and model
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
bert_model = BertModel.from_pretrained('bert-base-uncased')

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
bert_model = bert_model.to(device)

In [14]:
# Function to generate BERT embeddings for each sentence using attention mechanism.
def get_bert_embeddings(tokens):
    # Tokenize the entire sentence
    inputs = tokenizer(tokens, return_tensors='pt', is_split_into_words=True, padding=True, truncation=True)

    # Get BERT embeddings from the model
    with torch.no_grad():  # Disable gradient computation for efficiency
        outputs = bert_model(**inputs)

    # outputs.last_hidden_state gives the embeddings for each token in the sentence
    # Shape of outputs.last_hidden_state: (batch_size, sequence_length, hidden_size)
    token_embeddings = outputs.last_hidden_state.squeeze(0)  # Remove batch dimension, shape: (sequence_length, hidden_size)
    
    # The attention mechanism is already applied within the BERT model.
    # BERT outputs contextualized embeddings considering the entire sentence.
    
    # You can optionally aggregate the embeddings or return them as is.
    # Example: token_embeddings[i] gives the embedding for the i-th token in the sentence.
    
    return token_embeddings  # Shape: (sequence_length, hidden_size)

In [15]:
# Function to generate BERT embeddings for each sentence in the DataFrame
def generate_embeddings(df):
    embeddings_list = []
    for index, row in df.iterrows():
        tokenized_sentence = row['Tokens']
        embeddings = get_bert_embeddings(tokenized_sentence)
        embeddings_list.append(embeddings)
    return embeddings_list

In [16]:
embeddings_list = generate_embeddings(df)

In [17]:
# pad the embeddings to ensure uniformity across dataset as model will be trained in batches
padded_embeddings = pad_sequence(embeddings_list, batch_first=True)
df['Embeddings'] = [padded_embeddings[i] for i in range(padded_embeddings.shape[0])]
print(padded_embeddings.shape)

torch.Size([2500, 159, 768])


In [18]:
# encode the labels
label_encoder = LabelEncoder()
labels_list = ['ARG1', 'ARG2', 'REL', 'TIME', 'LOC', 'NONE', 'PADDING']
label_encoder.fit(labels_list)

df['Encoded_Labels'] = df['Labels'].apply(lambda x: label_encoder.transform(x.split()))

In [19]:
# Function to pad labels to max length
def pad_labels(labels, max_len, padding_label):
    # Initialize a tensor with the padding label (assuming integer encoding)
    padded_labels = torch.full((max_len,), padding_label, dtype=torch.long)
    
    # Fill in the actual labels up to the length of the original labels
    padded_labels[:len(labels)] = torch.tensor(labels, dtype=torch.long)
    
    return padded_labels

In [20]:
# Assuming 'PADDING' is already transformed to an integer (via label_encoder)
padding_label = label_encoder.transform(['PADDING'])[0]

# Get max length from the dataset
max_len = max(len(label) for label in df['Encoded_Labels'])

# Pad each list of encoded labels
padded_labels = [pad_labels(label, max_len, padding_label) for label in df['Encoded_Labels']]

# Add the padded labels to the DataFrame
df['Padded_Labels'] = padded_labels

In [21]:
# Split the data into training and testing sets
train_embeddings, val_embeddings, train_labels, val_labels = train_test_split(
    df['Embeddings'].tolist(),  
    df['Padded_Labels'].tolist(),
    test_size=0.2,
    random_state=42
)

In [22]:
# Convert lists of tensors to PyTorch tensors
train_dataset = TensorDataset(torch.stack(train_embeddings), torch.stack(train_labels))
val_dataset = TensorDataset(torch.stack(val_embeddings), torch.stack(val_labels))

# Create DataLoaders
train_loader = DataLoader(train_dataset, batch_size=32, shuffle=True)
val_loader = DataLoader(val_dataset, batch_size=32, shuffle=False)

In [23]:
label_to_idx = {label: idx for idx, label in enumerate(label_encoder.classes_)}
label_to_idx

{'ARG1': 0, 'ARG2': 1, 'LOC': 2, 'NONE': 3, 'PADDING': 4, 'REL': 5, 'TIME': 6}

In [24]:
train_dataset[0]

(tensor([[-1.0469, -0.2969, -0.2895,  ..., -0.3783, -0.0840,  0.2492],
         [-0.0087,  0.1263, -0.2467,  ..., -0.1116,  1.1379,  0.0720],
         [-0.6917, -0.6665, -0.1069,  ..., -0.7092,  0.0212,  0.2026],
         ...,
         [ 0.0000,  0.0000,  0.0000,  ...,  0.0000,  0.0000,  0.0000],
         [ 0.0000,  0.0000,  0.0000,  ...,  0.0000,  0.0000,  0.0000],
         [ 0.0000,  0.0000,  0.0000,  ...,  0.0000,  0.0000,  0.0000]]),
 tensor([0, 0, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 5, 5, 5, 3, 3, 3, 1, 1, 1,
         3, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4,
         4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4,
         4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4,
         4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4,
         4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4]))

In [25]:
class BiLSTM(nn.Module):
    def __init__(self, input_dim, hidden_dim, output_dim):
        super(BiLSTM, self).__init__()
        self.lstm = nn.LSTM(input_dim, hidden_dim, batch_first=True)
        self.hidden2tag = nn.Linear(hidden_dim, output_dim)
        self.softmax = nn.LogSoftmax(dim=-1)

    def forward(self, inputs):
        lstm_out, _ = self.lstm(inputs)
        emissions = self.hidden2tag(lstm_out)  # Shape: (batch_size, seq_len, output_dim)
        tag_scores = self.softmax(emissions)
        return tag_scores

# Define the model
input_dim = 768  # This would be the BERT embedding size
hidden_dim = 256
output_dim = len(labels_list)  # 7 labels in total

model = BiLSTM(input_dim, hidden_dim, output_dim)


In [26]:
loss_fn = nn.CrossEntropyLoss(ignore_index=label_to_idx['PADDING'], reduction='none')

optimizer = optim.Adam(model.parameters(), lr=0.001)
num_epochs = 200

# Training loop
for epoch in range(num_epochs):
    model.train()
    total_loss = 0
    
    for batch in train_loader:
        inputs, labels = batch  # Assuming inputs and labels are already padded
        
        # Forward pass through the model to get logits
        logits = model(inputs)  # Shape: [batch_size, seq_len, num_classes]
        
        # Make sure labels and logits have the same sequence length
        logits = logits[:, :labels.size(1), :]  # Truncate logits to match labels shape
        
        # Create mask for valid tokens (non-padding)
        mask = labels.ne(label_to_idx['PADDING'])  # Mask of shape [batch_size, seq_len]
        
        # Apply the mask to select valid tokens from logits and labels
        valid_logits = logits[mask]  # Shape: [num_valid_tokens, num_classes]
        valid_labels = labels[mask]  # Shape: [num_valid_tokens]
        
        # Compute loss only for valid tokens
        loss = loss_fn(valid_logits, valid_labels)
        
        # If the loss is not a scalar, compute its mean or sum
        if loss.dim() > 0:  # Check if loss is not a scalar
            loss = loss.mean()  # or use loss.sum() depending on your preference
        
        # Backpropagation
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()
        
        total_loss += loss.item()
    
    print(f"Epoch {epoch + 1}/{num_epochs}, Loss: {total_loss / len(train_loader)}")


Epoch 1/200, Loss: 1.0936160153812833
Epoch 2/200, Loss: 0.9802212317784628
Epoch 3/200, Loss: 0.9372138371543278
Epoch 4/200, Loss: 0.9054069708264063
Epoch 5/200, Loss: 0.8662827289293683
Epoch 6/200, Loss: 0.846226902235122
Epoch 7/200, Loss: 0.8234883736050318
Epoch 8/200, Loss: 0.7960568165022229
Epoch 9/200, Loss: 0.7709151336124965
Epoch 10/200, Loss: 0.7496250394790892
Epoch 11/200, Loss: 0.7237163961879791
Epoch 12/200, Loss: 0.7129293292287796
Epoch 13/200, Loss: 0.6893681032317025
Epoch 14/200, Loss: 0.6692477303837973
Epoch 15/200, Loss: 0.6506121196444072
Epoch 16/200, Loss: 0.6391044590208266
Epoch 17/200, Loss: 0.6214141041513473
Epoch 18/200, Loss: 0.6052105327447256
Epoch 19/200, Loss: 0.5973899799679953
Epoch 20/200, Loss: 0.5849008791976504
Epoch 21/200, Loss: 0.5732445153925154
Epoch 22/200, Loss: 0.5595219873246693
Epoch 23/200, Loss: 0.5477816192876725
Epoch 24/200, Loss: 0.5421354420601375
Epoch 25/200, Loss: 0.5322727173093765
Epoch 26/200, Loss: 0.5308100529133

In [27]:
def evaluate_bilstm(model, val_loader, criterion):
    model.eval()  # Set the model to evaluation mode
    total_loss = 0.0
    correct = 0
    total = 0
    
    with torch.no_grad():  # Disable gradient calculations
        for inputs, labels in val_loader:
            outputs = model(inputs)  # Forward pass
            
            # Ensure logits match the labels' shape
            outputs = outputs[:, :labels.size(1), :]  # Truncate outputs to match labels shape
            
            # Create mask for valid tokens (non-padding)
            mask = labels.ne(label_to_idx['PADDING'])  # Mask of shape [batch_size, seq_len]
            
            # Flatten outputs and labels for loss calculation
            valid_logits = outputs[mask]  # Shape: [num_valid_tokens, num_classes]
            valid_labels = labels[mask]  # Shape: [num_valid_tokens]
            
            # Calculate loss only for valid tokens
            loss = criterion(valid_logits, valid_labels)  # This returns a tensor of shape [num_valid_tokens]
            total_loss += loss.sum().item()  # Sum the individual losses to get total loss

            # Calculate predictions
            _, predicted = torch.max(outputs, dim=2)
            correct += (predicted[mask].view(-1) == labels[mask].view(-1)).sum().item()  # Only compare valid tokens
            total += mask.sum().item()  # Count only valid tokens

    avg_loss = total_loss / len(val_loader)  # Average loss per batch
    accuracy = correct / total if total > 0 else 0  # Avoid division by zero
    print(f'Validation Loss: {avg_loss:.4f}, Validation Accuracy: {accuracy:.4f}')
    return avg_loss, accuracy


In [28]:
val_loss, val_accuracy = evaluate_bilstm(model, val_loader, nn.CrossEntropyLoss(ignore_index=label_to_idx['PADDING'], reduction='none')
)

Validation Loss: 2663.4138, Validation Accuracy: 0.6078


In [29]:
def evaluate_bilstm_with_text_output(model, val_embeddings, val_labels, label_encoder):
    model.eval()  # Set model to evaluation mode
    with torch.no_grad():  # Disable gradient calculations
        for embeddings, true_labels in zip(val_embeddings, val_labels):
            embeddings = embeddings.unsqueeze(0)  # Add batch dimension
            true_labels = true_labels.unsqueeze(0)  # Add batch dimension

            # Forward pass through the model
            outputs = model(embeddings)  # Shape: [1, seq_length, num_labels]
            
            # Get predicted labels by selecting the max along the last dimension
            _, predicted_indices = torch.max(outputs, dim=2)
            
            # Convert predicted and true label indices to label names
            predicted_labels = label_encoder.inverse_transform(predicted_indices.squeeze(0).cpu().numpy())
            true_labels_text = label_encoder.inverse_transform(true_labels.squeeze(0).cpu().numpy())
            
            # Display the predicted and true labels
            print("Predicted Labels: ", predicted_labels)
            print("True Labels:      ", true_labels_text)
            print("-" * 50)

# Example usage:
evaluate_bilstm_with_text_output(model, train_embeddings, train_labels, label_encoder)


Predicted Labels:  ['ARG1' 'ARG1' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE'
 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'REL' 'REL' 'REL' 'NONE' 'NONE' 'NONE'
 'ARG2' 'ARG2' 'ARG2' 'NONE' 'NONE' 'NONE' 'ARG2' 'ARG2' 'NONE' 'NONE'
 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE'
 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE'
 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE'
 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE'
 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE'
 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE'
 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE'
 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE'
 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE'
 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE'
 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NONE' 'NON

In [40]:
# Testing with CaRB metric

In [41]:
def load_test_dataset(file_path):
    # Read the text file
    with open(file_path, 'r', encoding='utf-8') as file:
        sentences = file.readlines()

    # Clean up the sentences (strip whitespace characters like newline)
    sentences = [sentence.strip() for sentence in sentences]

    # Create a DataFrame
    df_test = pd.DataFrame(sentences, columns=['Sentence'])

    return df_test

df_test = load_test_dataset('./Dataset/test.txt')

In [42]:
df_test.head

<bound method NDFrame.head of                                               Sentence
0    32.7 % of all households were made up of indiv...
1    A CEN forms an important but small part of a L...
2    A Democrat , he became the youngest mayor in P...
3    A cafeteria is also located on the sixth floor...
4    A casting director at the time told Scott that...
..                                                 ...
636  `` Now everything '' -- such as program tradin...
637  `` The bottom line is that if we can get that ...
638  `` The only people who are flying are those wh...
639  `` To allow this massive level of unfettered f...
640    `` We were oversold and today we bounced back .

[641 rows x 1 columns]>

In [43]:
def generate_test_token(row):
    # Process the sentence with SpaCy
    doc = nlp(row['Sentence'])
    spacy_sentence = remerge_sent(doc)  # Assuming this function merges tokens as needed
    tokens = [token.text for token in spacy_sentence]

    return tokens  # Return the list of tokens

In [44]:
df_test['Tokens'] = df_test.apply(generate_test_token, axis=1)

In [45]:
df_test

Sentence  \
0    32.7 % of all households were made up of indiv...   
1    A CEN forms an important but small part of a L...   
2    A Democrat , he became the youngest mayor in P...   
3    A cafeteria is also located on the sixth floor...   
4    A casting director at the time told Scott that...   
..                                                 ...   
636  `` Now everything '' -- such as program tradin...   
637  `` The bottom line is that if we can get that ...   
638  `` The only people who are flying are those wh...   
639  `` To allow this massive level of unfettered f...   
640    `` We were oversold and today we bounced back .   

                                                Tokens  
0    [32.7, %, of, all, households, were, made, up,...  
1    [A, CEN, forms, an, important, but, small, par...  
2    [A, Democrat, ,, he, became, the, youngest, ma...  
3    [A, cafeteria, is, also, located, on, the, six...  
4    [A, casting, director, at, the, time, told, Sc...  
..                                                 ...  
636  [``, Now, everything, '', --, such, as, progra...  
637  [``, The, bottom, line, is, that, if, we, can,...  
638  [``, The, only, people, who, are, flying, are,...  
639  [``, To, allow, this, massive, level, of, unfe...  
640  [``, We, were, oversold, and, today, we, bounc...  

[641 rows x 2 columns]

In [46]:
embeddings_list_test = generate_embeddings(df_test)

In [47]:
# pad the embeddings to ensure uniformity across dataset as model will be trained in batches
padded_embeddings_test = pad_sequence(embeddings_list_test, batch_first=True)
df_test['Embeddings'] = [padded_embeddings_test[i] for i in range(padded_embeddings_test.shape[0])]
print(padded_embeddings_test.shape)

torch.Size([641, 70, 768])


In [48]:
# Create the reverse mapping from index to label
idx_to_label = {v: k for k, v in label_to_idx.items()}

def generate_extractions(model, padded_embeddings, df_test):
    model.eval()  # Set the model to evaluation mode
    with torch.no_grad():
        # Forward pass to get the logits from the model
        outputs = model(padded_embeddings)  # Assuming this gives logits of shape [batch_size, seq_len, num_classes]

    # Convert logits to predicted classes
    predicted_classes = torch.argmax(outputs, dim=-1)  # Get the predicted classes

    # Prepare the results
    results = []

    for i, row in df_test.iterrows():
        sentence = row['Sentence']
        tokens = row['Tokens']  # Use tokens from the 'Token' column
        n = len(tokens)  # Number of actual tokens in the sentence
        predicted_labels = predicted_classes[i][:n]  # Take only the first n predicted labels

        # Initialize the list for sentence results
        sentence_results = []
        current_rel = []  # Store current relation tokens
        arg1, arg2 = '', ''  # Initialize arguments

        for token_index in range(n):  # Iterate only through actual tokens
            predicted_class = predicted_labels[token_index]
            label = idx_to_label[predicted_class.item()]  # Map predicted class index to label

            if label != 'PADDING':
                if label == 'REL':
                    current_rel.append(tokens[token_index])  # Add to current relation tokens
                else:
                    # Process when encountering ARG1 or ARG2
                    if label == 'ARG1':
                        arg1 = tokens[token_index]
                    elif label == 'ARG2':
                        arg2 = tokens[token_index]

            # If we encounter a label that isn't REL and we have relation tokens, we finalize the current relation
            if current_rel and label != 'REL':
                # Append extraction in the required format if both arg1 and arg2 are found
                if arg1 and arg2:
                    rel = ' '.join(current_rel)  # Join relation tokens
                    sentence_results.append(f"{sentence}\t1\t{rel}\t{arg1}\t{arg2}")
                
                # Reset for next potential relation
                current_rel = []
                arg1, arg2 = '', ''  # Reset arguments

        # Check if there was an ongoing relation at the end of the loop
        if current_rel and arg1 and arg2:
            rel = ' '.join(current_rel)  # Join relation tokens
            sentence_results.append(f"{sentence}\t1\t{rel}\t{arg1}\t{arg2}")

        results.extend(sentence_results)

    return results

# Example usage
# Generate extractions
extractions = generate_extractions(model, padded_embeddings_test, df_test)

# Write to a tab-separated file
with open('../CaRB/system_outputs/test/extractions.txt', 'w') as f:
    for extraction in extractions:
        f.write(extraction + '\n')

print("Extraction file has been created.")

Extraction file has been created.
